In [120]:
import pandas as pd
import matplotlib as mpl
import geopandas as gpd
import pydeck as pdk
import requests

In [121]:
# get DTM and clean
# plot DTM
# get FIRMS for DTM bounds
# plot FIRMS
# pick 1 site
# get buffer
# plot timeseries of fire days
# plot timeseries of fire intensity
# compare years

In [122]:
dtm = pd.read_excel('inputs/DTM Nigeria Round 44 Dataset of Needs Monitoring Assessment for IDPs.xlsx', sheet_name='Needs Monitoring for IDPs')
dtm = dtm[dtm['Population Types'] =='IDPs in camp']
dtm = dtm[['Site Name ','Individuals (IND)','Longitude','Latitude']]

dtm = gpd.GeoDataFrame(dtm, geometry=gpd.points_from_xy(dtm.Longitude, dtm.Latitude), crs="EPSG:4326")

In [123]:
MAP_KEY = 'ede80fc572c8ff1367eb393f5a7550b0'

nigeria_url = 'https://firms.modaps.eosdis.nasa.gov/api/country/csv/' + MAP_KEY + '/MODIS_NRT/NGA/10'
firms_nigeria_10day = pd.read_csv(nigeria_url)
firms_nigeria_10day  = gpd.GeoDataFrame(firms_nigeria_10day , geometry=gpd.points_from_xy(firms_nigeria_10day.longitude, firms_nigeria_10day.latitude), crs="EPSG:4326")

firms_nigeria_historic = pd.read_csv('inputs/fire_archive_M-C61_409174.csv')
firms_nigeria_historic = gpd.GeoDataFrame(firms_nigeria_historic , geometry=gpd.points_from_xy(firms_nigeria_historic.longitude, firms_nigeria_historic.latitude), crs="EPSG:4326")

In [124]:
#| column: screen
# Define a layer to display on a map

# layer = pdk.Layer(
#     "ScatterplotLayer",
#     df,
#     pickable=True,
#     opacity=0.8,
#     stroked=True,
#     filled=True,
#     radius_scale=6,
#     radius_min_pixels=1,
#     radius_max_pixels=100,
#     line_width_min_pixels=1,
#     get_position="coordinates",
#     get_radius="exits_radius",
#     get_fill_color=[255, 140, 0],
#     get_line_color=[0, 0, 0],
# )
sites = pdk.Layer(
    "ScatterplotLayer",
    dtm,
    pickable=True,
    stroked=True,
    filled=True,
    extruded=False,
    radius_min_pixels=5,
    get_position="geometry.coordinates",
    #get_fill_color="[255, 140, 0]",
    #get_line_color=[255, 255, 255],
    line_width_min_pixels=1,
    get_size=1000,
    get_color=[1, 51, 160],

)
fires = pdk.Layer(
    "ScatterplotLayer",
    firms_nigeria_10day,
    pickable=False,
    stroked=False,
    filled=True,
    extruded=False,
    radius_min_pixels=5,
    get_position="geometry.coordinates",
    get_size=1000,
    get_fill_color="[215, 41, 47]",
    #get_line_color=[255, 255, 255],
    line_width_min_pixels=1,
)

# Set the viewport location 35.621109,33.514613 13.157158,11.836775
view_state = pdk.ViewState(latitude=11.836775, longitude=13.157158, zoom=9, bearing=0, pitch=0)

# Render
r = pdk.Deck(layers=[sites, fires], initial_view_state=view_state, tooltip={"html": "<b>Site ID:</b> {SiteID_SC}""</br><b>Site ID other:</b> {SiteID_other}""</br><b>Name:</b> {Site_name_en}""</br><b>Capacity:</b> {capacity} individuals""</br><b>Occupancy:</b> {occupancy} individuals""</br><b>Cadaster:</b> {admin3Name}""</br><b>Source:</b> {source}", "style": {"backgroundColor": "#f6f7ec","color": "#195b71"}})
r.to_html("sites.html")

In [ ]:
dtm = dtm.to_crs("EPSG:32631")

firms_nigeria_historic = firms_nigeria_historic.to_crs("EPSG:32631")

dtm['geometry'] = dtm['geometry'].buffer(100)

intersection = gpd.sjoin(dtm, firms_nigeria_historic, how='inner')

In [130]:
intersection.explore()

In [131]:
len(dtm)

290

In [132]:
len(firms_nigeria_historic)

174032

In [141]:
test = gpd.sjoin(firms_nigeria_historic, dtm, how='inner')

In [142]:
test

latitude  longitude  brightness  scan  track    acq_date  acq_time  \
38744    12.6724    13.6042       324.3   1.0    1.0  2021-01-29      1238   
38744    12.6724    13.6042       324.3   1.0    1.0  2021-01-29      1238   
62062    12.6775    13.6039       382.8   1.3    1.1  2021-04-30      1220   
67957    11.8730    13.2504       329.9   2.5    1.5  2021-11-07      1007   
128695   13.6739    13.3284       333.1   1.1    1.1  2022-03-07      1226   
133116   13.6713    13.3319       337.9   1.0    1.0  2022-06-07       936   

       satellite instrument  confidence  ...  bright_t31    frp  daynight  \
38744       Aqua      MODIS          53  ...       310.3    5.3         D   
38744       Aqua      MODIS          53  ...       310.3    5.3         D   
62062       Aqua      MODIS         100  ...       318.8  202.1         D   
67957      Terra      MODIS          75  ...       304.4   62.7         D   
128695      Aqua      MODIS          41  ...       318.6   10.4         D   
133116     Terra      MODIS          77  ...       318.8   14.7         D   

       type                         geometry index_right  \
38744     2  POINT (1657447.167 1424605.239)        1591   
38744     2  POINT (1657447.167 1424605.239)        1588   
62062     2  POINT (1657390.541 1425176.748)        1592   
67957     0  POINT (1621894.324 1333322.392)        1153   
128695    0  POINT (1622371.482 1535767.796)         872   
133116    0  POINT (1622768.113 1535492.582)         872   

                                    Site Name  Individuals (IND)  Longitude  \
38744                                Vertinary              3909   13.60732   
38744   Government Day Secondary School (Gdss)              4364   13.60538   
62062                       Fulatari Camp Camp              9130   13.60258   
67957                           Muna El Badawy             50310   13.24972   
128695                Mallam Fatori Kessa Camp              3025   13.33060   
133116                Mallam Fatori Kessa Camp              3025   13.33060   

        Latitude  
38744   12.66993  
38744   12.67282  
62062   12.68097  
67957   11.87186  
128695  13.67065  
133116  13.67065  

[6 rows x 21 columns]

In [135]:
len(test)

174033

In [136]:
test.to_excel('test3.xlsx')

In [137]:
intersection.head(5)

Site Name   Individuals (IND)  Longitude  \
872                 Mallam Fatori Kessa Camp               3025   13.33060   
872                 Mallam Fatori Kessa Camp               3025   13.33060   
1153                          Muna El Badawy              50310   13.24972   
1588  Government Day Secondary School (Gdss)               4364   13.60538   
1591                               Vertinary               3909   13.60732   

      Latitude                                           geometry  \
872   13.67065  POLYGON ((1623128.604 1535413.493, 1623126.197...   
872   13.67065  POLYGON ((1623128.604 1535413.493, 1623126.197...   
1153  11.87186  POLYGON ((1622323.921 1333191.657, 1622321.514...   
1588  12.67282  POLYGON ((1658075.376 1424657.764, 1658072.968...   
1591  12.66993  POLYGON ((1658302.686 1424341.927, 1658300.278...   

      index_right  latitude  longitude  brightness  scan  ...    acq_date  \
872        133116   13.6713    13.3319       337.9   1.0  ...  2022-06-07   
872        128695   13.6739    13.3284       333.1   1.1  ...  2022-03-07   
1153        67957   11.8730    13.2504       329.9   2.5  ...  2021-11-07   
1588        38744   12.6724    13.6042       324.3   1.0  ...  2021-01-29   
1591        38744   12.6724    13.6042       324.3   1.0  ...  2021-01-29   

     acq_time  satellite instrument confidence  version  bright_t31   frp  \
872       936      Terra      MODIS         77     6.03       318.8  14.7   
872      1226       Aqua      MODIS         41     6.03       318.6  10.4   
1153     1007      Terra      MODIS         75     6.03       304.4  62.7   
1588     1238       Aqua      MODIS         53     6.03       310.3   5.3   
1591     1238       Aqua      MODIS         53     6.03       310.3   5.3   

      daynight type  
872          D    0  
872          D    0  
1153         D    0  
1588         D    2  
1591         D    2  

[5 rows x 21 columns]

In [139]:
intersection.groupby('Site Name ')['Site Name '].count().sort_values(ascending=False)

Site Name 
Mallam Fatori Kessa Camp                  2
Fulatari Camp Camp                        1
Government Day Secondary School (Gdss)    1
Muna El Badawy                            1
Vertinary                                 1
Name: Site Name , dtype: int64

In [140]:
intersection.columns.to_list()

['Site Name ',
 'Individuals (IND)',
 'Longitude',
 'Latitude',
 'geometry',
 'index_right',
 'latitude',
 'longitude',
 'brightness',
 'scan',
 'track',
 'acq_date',
 'acq_time',
 'satellite',
 'instrument',
 'confidence',
 'version',
 'bright_t31',
 'frp',
 'daynight',
 'type']

In [ ]:
firms_nigeria_10day.explore(color='red', tiles='CartoDB dark_matter')

In [ ]:
test3 = intersection.to_crs('EPSG:4326')
dtm2 = dtm.to_crs('EPSG:4326')

In [ ]:
#| column: screen
# Define a layer to display on a map

# layer = pdk.Layer(
#     "ScatterplotLayer",
#     df,
#     pickable=True,
#     opacity=0.8,
#     stroked=True,
#     filled=True,
#     radius_scale=6,
#     radius_min_pixels=1,
#     radius_max_pixels=100,
#     line_width_min_pixels=1,
#     get_position="coordinates",
#     get_radius="exits_radius",
#     get_fill_color=[255, 140, 0],
#     get_line_color=[0, 0, 0],
# )
sites = pdk.Layer(
    "GeoJsonLayer",
    dtm2,
    pickable=True,
    stroked=True,
    filled=True,
    extruded=False,
    radius_min_pixels=5,
    get_position="geometry.coordinates",
    #get_fill_color="[255, 140, 0]",
    #get_line_color=[255, 255, 255],
    line_width_min_pixels=1,


)
fires = pdk.Layer(
    "GeoJsonLayer",
    test3,
    pickable=False,
    stroked=False,
    filled=True,
    extruded=False,
    radius_min_pixels=5,
    get_position="geometry.coordinates",
    get_size=1000,
    get_fill_color="[215, 41, 47]",
    #get_line_color=[255, 255, 255],
    line_width_min_pixels=1,
)

# Set the viewport location 35.621109,33.514613 13.157158,11.836775
view_state = pdk.ViewState(latitude=11.836775, longitude=13.157158, zoom=9, bearing=0, pitch=0)

# Render
r = pdk.Deck(layers=[sites, fires], initial_view_state=view_state, tooltip={"html": "<b>Site ID:</b> {SiteID_SC}""</br><b>Site ID other:</b> {SiteID_other}""</br><b>Name:</b> {Site_name_en}""</br><b>Capacity:</b> {capacity} individuals""</br><b>Occupancy:</b> {occupancy} individuals""</br><b>Cadaster:</b> {admin3Name}""</br><b>Source:</b> {source}", "style": {"backgroundColor": "#f6f7ec","color": "#195b71"}})
r
#r.to_html("sites.html")

In [ ]:
test3